In [1]:
%%capture

import warnings
warnings.filterwarnings("ignore")

import altair as alt
import calitp_data_analysis.magics
import pandas as pd
import sys
sys.path.append("../../bus_service_increase")
sys.path.append("../")
import annual_ridership_module
from bus_service_utils import chart_utils
from calitp_data_analysis import calitp_color_palette as cp
from IPython.display import HTML, Markdown, display
from update_vars import GCS_FILE_PATH, MONTH, PUBLIC_FILENAME, YEAR
from _01_ntd_ridership_utils import sum_by_group

# from shared_utils.rt_dates import MONTH_DICT

# alt.renderers.enable("html")
alt.data_transformers.enable("default", max_rows=None)

WIDTH = 300
HEIGHT = 150

In [2]:
# parameters cell for local
rtpa = "Metropolitan Transportation Commission"

In [3]:
# Parameters
rtpa = "Metropolitan Transportation Commission"


In [4]:
%%capture_parameters
rtpa

# Metropolitan Transportation Commission
## Annual Ridership Trends

**Download data from our public [folder](https://console.cloud.google.com/storage/browser/calitp-publish-data-analysis)** by navigating to `ntd_annual_ridership` and selecting a file.

Transit operators/agencies that submit annual reports to NTD are included in this report. Reporters that were previously active reporters, but are currently not, may appear. This may result in Reporters showing zero or partial ridership data in the report. 

If a Reporter, type of service, mode, or any combination of, is not a annual reporter or has not reported data since 2018, they will not appear in the report.

Examples: 
- **Reporter A** is an annual reporter from 2019-2022, then became inactive and did not report for 2023. Reporter A's ridership data will be displayed for 2019-2022 only.
- **Reporter B** is an annual from 2000-2017, then became inactive and did not report for 2018. Reporter B will be named in the report, but will not display ridership data.
- **Reporter C** was an inactive reporter form 2015-2020, then became an active full reporter for 2021. Reporter C's ridership data will be displayed for 2021-present. 

In [5]:
URL = "https://console.cloud.google.com/storage/" "browser/calitp-publish-data-analysis"

display(
    HTML(
        f"""
        <a href={URL}>
        Download the latest month of data: {PUBLIC_FILENAME}</a>
        """
    )
)

In [6]:
# read in data
df = pd.read_parquet(
    f"{GCS_FILE_PATH}annual_ridership_report_data.parquet",
    filters=[("rtpa_name", "==", rtpa)],
)

In [7]:
def group_by_agency(df):
    """
    Take in the 'by_ageny_long' df and aggregatese by rtpa, and calculates upt % of total.
    To be used in pie chart
    """
    initial_agg = df.groupby("source_agency").agg(total_upt=("upt", "sum")).reset_index()

    # % total columns
    initial_agg["pct_of_total_upt"] = (
        initial_agg["total_upt"] / initial_agg["total_upt"].sum()
    ) * 100

    # cleaning data types and rounding
    initial_agg["total_upt"] = initial_agg["total_upt"].astype("int64")
    initial_agg["pct_of_total_upt"] = initial_agg["pct_of_total_upt"].round(decimals=2)
    cleaned_agg = initial_agg.sort_values(by="total_upt", ascending=False)

    return cleaned_agg

In [8]:
def make_line_chart(
    df: pd.DataFrame,
    y_col: str,
    color_col: str,
    title: str,
) -> alt.Chart:
    df = df[df[y_col] > 0].dropna(subset=y_col)

    # x_label = [i for i in df.report_year.unique() if
    #           any(substring in i for substring in
    #               ["-01", "-06"])
    #          ]

    chart = (
        (
            alt.Chart(df)
            .mark_line(point=True)
            .encode(
                x=alt.X(
                    "year:O",
                    # axis=alt.Axis(values = x_label),
                    title="Date",
                ),
                y=alt.Y(y_col, title=y_col),
                color=alt.Color(
                    color_col,
                    # title = "",
                    scale=alt.Scale(
                        range=cp.CALITP_CATEGORY_BRIGHT_COLORS
                        + cp.CALITP_CATEGORY_BOLD_COLORS
                    ),
                ),
                tooltip=["year", y_col, color_col, "rtpa_name"],
            )
            .properties(width=WIDTH, height=HEIGHT)
            .facet(color_col, columns=2, title="")
            .resolve_scale(y="independent")
        )
        .properties(title=title)
        .interactive()
    )

    return chart

In [9]:
def make_bar_chart(
    df: pd.DataFrame,
    y_col: str,
    color_col: str,
    title: str,
) -> alt.Chart:

    def short_label(word):
        shorten_dict = {
            "change_1yr": "Change",
            "pct_change_1yr": "Change",
        }
        return shorten_dict[word]

    # For change column, we are missing everything prior to 2023
    # df = df.dropna(subset = y_col)

    # need flag for y_col >,<, 0, missing?
    # count function to how many agencies fall in those categories, then look at those agencies
    # present table

    # x_label = [i for i in df.report_year.unique() if
    #           any(substring in i for substring in
    #               ["-01", "-03", "-06", "-09"])
    #          ]

    chart = (
        (
            alt.Chart(df)
            .mark_bar()
            .encode(
                x=alt.X(
                    "year:O",
                    # axis=alt.Axis(values = x_label),
                    title="Date",
                ),
                y=alt.Y(y_col, title=y_col),
                color=alt.Color(
                    color_col,
                    title="",
                    scale=alt.Scale(
                        range=cp.CALITP_CATEGORY_BRIGHT_COLORS
                        + cp.CALITP_CATEGORY_BOLD_COLORS
                    ),
                ),
                tooltip=["year", y_col, color_col, "rtpa_name"],
            )
            .properties(width=WIDTH, height=HEIGHT)
            .facet(color_col, columns=2, title="")
            .resolve_scale(x="shared", y="independent")
        )
        .properties(title=title)
        .interactive()
    )

    return chart

In [10]:
def make_pie_chart(df, col, color_col):

    pie = (
        alt.Chart(df)
        .mark_arc(radius=150)
        .encode(
            theta=col,
            color=color_col,
            tooltip=["source_agency", "total_upt", "pct_of_total_upt"],
        )
        .properties(
            title=f"Total Annual Unlinked Passenger Trips per Reporter in RTPA since 2018",
        )
    )

    return pie

In [11]:
# simple bar chart for total agencies and UPT
def total_upt_chart(df: pd.DataFrame, x_col: str, y_col: str, tool_tip: list):
    bar_chart = (
        alt.Chart(df)
        .mark_bar()
        .encode(
            x=alt.X(x_col).sort("-y"),
            y=alt.Y(y_col),
            tooltip=tool_tip,
            color=alt.Color(
                x_col,
                title="",
                scale=alt.Scale(
                    range=cp.CALITP_CATEGORY_BRIGHT_COLORS
                    + cp.CALITP_CATEGORY_BOLD_COLORS
                ),
            ),
        )
        .properties(
            title=f"Total Annual Unlinked Passenger Trips per Reporter in RTPA since 2018",
            width=WIDTH,
            height=HEIGHT,
        )
        .resolve_scale(y="independent")
        .interactive()
    )

    return bar_chart

In [12]:
agency_cols = ["ntd_id", "source_agency", "rtpa_name"]
mode_cols = ["mode_full", "rtpa_name"]
tos_cols = ["service_full", "rtpa_name"]
reporter_type_cols = ["reporter_type", "rtpa_name"]

annual_group_col_2 = ["year"]

annual_agg_col= {
                            "upt": "sum",
                            "previous_y_upt": "sum",
                            "change_1yr": "sum",
                        }
annual_change_col ="previous_y_upt"

# by_agency_long = sum_by_group(df, group_cols=agency_cols, agg_cols)
# by_mode_long = sum_by_group(df, mode_cols)
# by_tos_long = sum_by_group(df, tos_cols)
# by_reporter_type_long = sum_by_group(df, reporter_type_cols)

by_agency_long = sum_by_group(
                df = df,
                group_cols= agency_cols,
                group_col2= annual_group_col_2,# look into combingin with base grou_cols
                agg_cols = annual_agg_col,
                change_col = annual_change_col
            )

by_mode_long = sum_by_group(
                df = df,
                group_cols= mode_cols,
                group_col2= annual_group_col_2,# look into combingin with base grou_cols
                agg_cols = annual_agg_col,
                change_col = annual_change_col
            )
    
by_tos_long = sum_by_group(
                df = df,
                group_cols= tos_cols,
                group_col2= annual_group_col_2,# look into combingin with base grou_cols
                agg_cols = annual_agg_col,
                change_col = annual_change_col
            )
by_reporter_type_long = sum_by_group(
                df = df,
                group_cols= reporter_type_cols,
                group_col2= annual_group_col_2,# look into combingin with base grou_cols
                agg_cols = annual_agg_col,
                change_col = annual_change_col
            )

In [13]:
# agg by agency, for pie chart
agency_agg_yr = group_by_agency(by_agency_long)

# total UPT check
total_upt = by_agency_long["upt"].sum()
agency_count = by_agency_long["source_agency"].nunique()

### Report Totals

In [14]:
Markdown(
    f"""
Within {rtpa}:
- Number of Reporters: <b>{agency_count}</b>.
- Total Unlinked Passenger Trips since the beginning of this report: <b>{total_upt:,}</b>.
- Individual Reporters ridership breakdown:
"""
)


Within Metropolitan Transportation Commission:
- Number of Reporters: <b>25</b>.
- Total Unlinked Passenger Trips since the beginning of this report: <b>2,009,957,677.0</b>.
- Individual Reporters ridership breakdown:


In [15]:
display(agency_agg_yr.reset_index(drop=True))

source_agency  total_upt  \
0   City and County of San Francisco (SFMTA) - Tra...  922569306   
1   San Francisco Bay Area Rapid Transit District ...  455096497   
2               Alameda-Contra Costa Transit District  238095061   
3   Santa Clara Valley Transportation Authority (VTA)  156318886   
4       Peninsula Corridor Joint Powers Board (PCJPB)   63666313   
5           San Mateo County Transit District (SMCTD)   52923694   
6   Golden Gate Bridge, Highway and Transportation...   20383349   
7      Central Contra Costa Transit Authority (CCCTA)   15567938   
8                Marin County Transit District (MCTD)   15158172   
9   San Francisco Bay Area Water Emergency Transpo...   11893820   
10         The Eastern Contra Costa Transit Authority    8976036   
11              City of Santa Rosa - Transit Division    8337332   
12  Livermore / Amador Valley Transit Authority (L...    7267092   
13                              Solano County Transit    5882991   
14    Western Contra Costa Transit Authority (WCCTA )    4881988   
15  County of Sonoma (SCT) - Department of Public ...    4238328   
16        Napa Valley Transportation Authority (NVTA)    4227825   
17  City of Fairfield, California - Transportation...    3522157   
18    Sonoma-Marin Area Rail Transit District (SMART)    3037255   
19  Metropolitan Transportation Commission (MTC) -...    2999062   
20     City of Vacaville - Department of Public Works    1697248   
21                         City of Petaluma - Transit    1511625   
22            City of Union City (UCT) - Public Works    1414508   
23                       City of Dixon - Public Works     249467   
24     City of Rio Vista - Department of Public Works      41727   

    pct_of_total_upt  
0              45.90  
1              22.64  
2              11.85  
3               7.78  
4               3.17  
5               2.63  
6               1.01  
7               0.77  
8               0.75  
9               0.59  
10              0.45  
11              0.41  
12              0.36  
13              0.29  
14              0.24  
15              0.21  
16              0.21  
17              0.18  
18              0.15  
19              0.15  
20              0.08  
21              0.08  
22              0.07  
23              0.01  
24              0.00

In [16]:
tooltip_list = ["source_agency", "total_upt", "pct_of_total_upt"]

total_upt_chart(
    agency_agg_yr, 
    x_col="source_agency", 
    y_col="total_upt", 
    tool_tip=tooltip_list
)

alt.Chart(...)

### Agency

In [17]:
make_line_chart(
    by_agency_long,
    y_col="upt",
    color_col="source_agency",
    title="Total Annual Unlinked Passenger Trips by Reporter",
)

alt.FacetChart(...)

In [18]:
make_bar_chart(
    by_agency_long,
    y_col="change_1yr",
    color_col="source_agency",
    title="Yearly Change in Unlinked Passenger Trips by Agency",
)

alt.FacetChart(...)

## Transit Mode

In [19]:
make_line_chart(
    by_mode_long, 
    y_col="upt", 
    color_col="mode_full", 
    title="Total Annual UPT by Mode"
)

alt.FacetChart(...)

In [20]:
make_bar_chart(
    by_mode_long,
    y_col="change_1yr",
    color_col="mode_full",
    title="Yearly Change in UPT by Mode",
)

alt.FacetChart(...)

## Type of Service

In [21]:
make_line_chart(
    by_tos_long,
    y_col="upt",
    color_col="service_full",
    title="Total Annual UPT by Type of Service",
)

alt.FacetChart(...)

In [22]:
make_bar_chart(
    by_tos_long,
    y_col="change_1yr",
    color_col="service_full",
    title="Total Change in UPT by Type of Service",
)

alt.FacetChart(...)

## Reporter Type

In [23]:
make_line_chart(
    by_reporter_type_long,
    y_col="upt",
    color_col="reporter_type",
    title="Total Annual UPT by NTD Reporter Type",
)

alt.FacetChart(...)

In [24]:
make_bar_chart(
    by_reporter_type_long,
    y_col="change_1yr",
    color_col="reporter_type",
    title="Total Annual UPT by NTD Reporter Type",
)

alt.FacetChart(...)